In [17]:
import pandas as pd
import re
import requests
from bs4 import BeautifulSoup
import unicodedata

from selenium import webdriver
from selenium.webdriver.common.keys import Keys

#from tqdm import tqdm_notebook as tqdm

from pw import username
from pw import password

In [28]:
#import tqdm.notebook as tqdm

In [2]:
def scrape(url):
    page = requests.get(url)
    soup = BeautifulSoup(page.text, 'html.parser')
    return soup

In [3]:
url = "https://www.whiskybase.com/account/login?return=https%3A%2F%2Fwww.whiskybase.com%2Fwhiskies%2Ftop1000"
driver = webdriver.Chrome('/Users/chrisriggio/Downloads/chromedriver')
driver.get(url)

# Using selenium to log into the site with provided username/password
element = driver.find_element_by_name("username")
element.click()
element.send_keys(username)
element = driver.find_element_by_name("password")
element.click()
element.send_keys(password)
element.send_keys(Keys.ENTER)



url = 'https://www.whiskybase.com/whiskies/new-releases'
driver.get(url)
soup = BeautifulSoup(driver.page_source, 'html.parser')


#element.click('https://www.whiskybase.com/whiskies/new-releases')
# Using selenium to go to the webpage where I want to scrape the data from
#whiskybase = scrape('https://www.whiskybase.com/whiskies/new-releases')

In [4]:
soup

<html class="js" lang="en"><head>
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<script async="" src="https://www.google-analytics.com/analytics.js"></script><script>document.documentElement.className += 'js'</script>
<link href="https://assets.whiskybase.com/assets/css/wb.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://assets.whiskybase.com/assets/css/themes/base.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://assets.whiskybase.com/assets/css/imagezoom.css?20191129" rel="stylesheet" type="text/css"/>
<link href="https://www.whiskybase.com/whiskies/new-releases" rel="canonical"/>
<title>New releases - Whiskybase - Ratings and reviews for whisky</title>
<meta content="#7f7a4a" name="theme-color"/>
<meta content="#7f7a4a" name="msapplication-navbutton-color"/>
<meta content="#7f7a4a" name="apple-mobile-web-app-status-bar-style"/>
<meta content="Whiskybase: discover new bottles, track your collecti

In [5]:
cols = soup.find_all('tr')

In [6]:
col_comp = [cols[0].find_all('th')[col].text[14:-12] for col in range(1,8)]
col_comp

['Name', 'Stated Age', 'Strength', 'Size', 'Bottled', 'Casknumber', 'Rating']

In [7]:
#names
soup.find_all('a', {'class': 'clickable'})[0].text

'10th Street Peated Single Malt '

In [8]:
#td class="data text-right">
test1 = soup.find_all('td')
test1[7].text#[1:-2]

'94.00'

In [9]:
#a class="sort"
soup.find_all('td')[0]

<td class="photo buttons">
<a class="photo photo-popup" data-photo="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg" href="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg"><img alt="10th Street Peated Single Malt" class="bottle-preview small unveil" data-src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png" onerror="this.parentElement.style.display='none';this.parentElement.classList.remove('photo-popup');" src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png"/></a>
</td>

In [10]:
#a class="photo photo-popup"
soup.find_all('a', {'class': 'photo photo-popup'})[0]

<a class="photo photo-popup" data-photo="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg" href="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-big.jpg"><img alt="10th Street Peated Single Malt" class="bottle-preview small unveil" data-src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png" onerror="this.parentElement.style.display='none';this.parentElement.classList.remove('photo-popup');" src="https://static.whiskybase.com/storage/whiskies/1/3/5873/230090-small.png"/></a>

In [11]:
#a class="clickable" 
soup.find_all('a', {'class': 'clickable'})[0].text

'10th Street Peated Single Malt '

In [30]:
whisky_num = len(soup.find_all('a', {'class': 'clickable'}))

In [31]:
len(soup.find_all('a', {'class': 'clickable'}))

5391

In [32]:
namelist = []

for i in range(0, whisky_num):
    name = soup.find_all('a', {'class': 'clickable'})[i].text
    namelist.append(name)
    print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


In [64]:
#td class="data text-right"
soup.find_all('td', {'class': 'data text-right'})[40].text

'16'

In [33]:
# names = pd.DataFrame(namelist, columns=['Name'])
# names.to_csv('whiskybase_names.csv')

In [71]:
stated_age = []
for i in range(0, len(soup.find_all('td', {'class': 'data text-right'})), 8):
    age = soup.find_all('td', {'class': 'data text-right'})[i].text
    if age == '':
        stated_age.append(None)
    else:
        stated_age.append(age)
    print(i)

0
8
16
24
32
40
48
56
64
72
80
88
96
104
112
120
128
136
144
152
160
168
176
184
192
200
208
216
224
232
240
248
256
264
272
280
288
296
304
312
320
328
336
344
352
360
368
376
384
392
400
408
416
424
432
440
448
456
464
472
480
488
496
504
512
520
528
536
544
552
560
568
576
584
592
600
608
616
624
632
640
648
656
664
672
680
688
696
704
712
720
728
736
744
752
760
768
776
784
792
800
808
816
824
832
840
848
856
864
872
880
888
896
904
912
920
928
936
944
952
960
968
976
984
992
1000
1008
1016
1024
1032
1040
1048
1056
1064
1072
1080
1088
1096
1104
1112
1120
1128
1136
1144
1152
1160
1168
1176
1184
1192
1200
1208
1216
1224
1232
1240
1248
1256
1264
1272
1280
1288
1296
1304
1312
1320
1328
1336
1344
1352
1360
1368
1376
1384
1392
1400
1408
1416
1424
1432
1440
1448
1456
1464
1472
1480
1488
1496
1504
1512
1520
1528
1536
1544
1552
1560
1568
1576
1584
1592
1600
1608
1616
1624
1632
1640
1648
1656
1664
1672
1680
1688
1696
1704
1712
1720
1728
1736
1744
1752
1760
1768
1776
1784
1792
1800
1808
1816


12784
12792
12800
12808
12816
12824
12832
12840
12848
12856
12864
12872
12880
12888
12896
12904
12912
12920
12928
12936
12944
12952
12960
12968
12976
12984
12992
13000
13008
13016
13024
13032
13040
13048
13056
13064
13072
13080
13088
13096
13104
13112
13120
13128
13136
13144
13152
13160
13168
13176
13184
13192
13200
13208
13216
13224
13232
13240
13248
13256
13264
13272
13280
13288
13296
13304
13312
13320
13328
13336
13344
13352
13360
13368
13376
13384
13392
13400
13408
13416
13424
13432
13440
13448
13456
13464
13472
13480
13488
13496
13504
13512
13520
13528
13536
13544
13552
13560
13568
13576
13584
13592
13600
13608
13616
13624
13632
13640
13648
13656
13664
13672
13680
13688
13696
13704
13712
13720
13728
13736
13744
13752
13760
13768
13776
13784
13792
13800
13808
13816
13824
13832
13840
13848
13856
13864
13872
13880
13888
13896
13904
13912
13920
13928
13936
13944
13952
13960
13968
13976
13984
13992
14000
14008
14016
14024
14032
14040
14048
14056
14064
14072
14080
14088
14096
14104
1411

23712
23720
23728
23736
23744
23752
23760
23768
23776
23784
23792
23800
23808
23816
23824
23832
23840
23848
23856
23864
23872
23880
23888
23896
23904
23912
23920
23928
23936
23944
23952
23960
23968
23976
23984
23992
24000
24008
24016
24024
24032
24040
24048
24056
24064
24072
24080
24088
24096
24104
24112
24120
24128
24136
24144
24152
24160
24168
24176
24184
24192
24200
24208
24216
24224
24232
24240
24248
24256
24264
24272
24280
24288
24296
24304
24312
24320
24328
24336
24344
24352
24360
24368
24376
24384
24392
24400
24408
24416
24424
24432
24440
24448
24456
24464
24472
24480
24488
24496
24504
24512
24520
24528
24536
24544
24552
24560
24568
24576
24584
24592
24600
24608
24616
24624
24632
24640
24648
24656
24664
24672
24680
24688
24696
24704
24712
24720
24728
24736
24744
24752
24760
24768
24776
24784
24792
24800
24808
24816
24824
24832
24840
24848
24856
24864
24872
24880
24888
24896
24904
24912
24920
24928
24936
24944
24952
24960
24968
24976
24984
24992
25000
25008
25016
25024
25032
2504

34640
34648
34656
34664
34672
34680
34688
34696
34704
34712
34720
34728
34736
34744
34752
34760
34768
34776
34784
34792
34800
34808
34816
34824
34832
34840
34848
34856
34864
34872
34880
34888
34896
34904
34912
34920
34928
34936
34944
34952
34960
34968
34976
34984
34992
35000
35008
35016
35024
35032
35040
35048
35056
35064
35072
35080
35088
35096
35104
35112
35120
35128
35136
35144
35152
35160
35168
35176
35184
35192
35200
35208
35216
35224
35232
35240
35248
35256
35264
35272
35280
35288
35296
35304
35312
35320
35328
35336
35344
35352
35360
35368
35376
35384
35392
35400
35408
35416
35424
35432
35440
35448
35456
35464
35472
35480
35488
35496
35504
35512
35520
35528
35536
35544
35552
35560
35568
35576
35584
35592
35600
35608
35616
35624
35632
35640
35648
35656
35664
35672
35680
35688
35696
35704
35712
35720
35728
35736
35744
35752
35760
35768
35776
35784
35792
35800
35808
35816
35824
35832
35840
35848
35856
35864
35872
35880
35888
35896
35904
35912
35920
35928
35936
35944
35952
35960
3596

In [74]:
len(stated_age)

5391

In [62]:
list(range(0,89, 8))

[0, 8, 16, 24, 32, 40, 48, 56, 64, 72, 80, 88]

In [70]:
len(soup.find_all('td', {'class': 'data text-right'}))

43128

In [99]:
numb = len(soup.find_all('td', {'class': 'data text-right'}))

In [100]:
strength = []
for i in range(1, numb, 8):
    vol = soup.find_all('td', {'class': 'data text-right'})[i].text
    if vol == '':
        strength.append(None)
    else:
        strength.append(vol)
    print(i)

1
9
17
25
33
41
49
57
65
73
81
89
97
105
113
121
129
137
145
153
161
169
177
185
193
201
209
217
225
233
241
249
257
265
273
281
289
297
305
313
321
329
337
345
353
361
369
377
385
393
401
409
417
425
433
441
449
457
465
473
481
489
497
505
513
521
529
537
545
553
561
569
577
585
593
601
609
617
625
633
641
649
657
665
673
681
689
697
705
713
721
729
737
745
753
761
769
777
785
793
801
809
817
825
833
841
849
857
865
873
881
889
897
905
913
921
929
937
945
953
961
969
977
985
993
1001
1009
1017
1025
1033
1041
1049
1057
1065
1073
1081
1089
1097
1105
1113
1121
1129
1137
1145
1153
1161
1169
1177
1185
1193
1201
1209
1217
1225
1233
1241
1249
1257
1265
1273
1281
1289
1297
1305
1313
1321
1329
1337
1345
1353
1361
1369
1377
1385
1393
1401
1409
1417
1425
1433
1441
1449
1457
1465
1473
1481
1489
1497
1505
1513
1521
1529
1537
1545
1553
1561
1569
1577
1585
1593
1601
1609
1617
1625
1633
1641
1649
1657
1665
1673
1681
1689
1697
1705
1713
1721
1729
1737
1745
1753
1761
1769
1777
1785
1793
1801
1809
1817


12785
12793
12801
12809
12817
12825
12833
12841
12849
12857
12865
12873
12881
12889
12897
12905
12913
12921
12929
12937
12945
12953
12961
12969
12977
12985
12993
13001
13009
13017
13025
13033
13041
13049
13057
13065
13073
13081
13089
13097
13105
13113
13121
13129
13137
13145
13153
13161
13169
13177
13185
13193
13201
13209
13217
13225
13233
13241
13249
13257
13265
13273
13281
13289
13297
13305
13313
13321
13329
13337
13345
13353
13361
13369
13377
13385
13393
13401
13409
13417
13425
13433
13441
13449
13457
13465
13473
13481
13489
13497
13505
13513
13521
13529
13537
13545
13553
13561
13569
13577
13585
13593
13601
13609
13617
13625
13633
13641
13649
13657
13665
13673
13681
13689
13697
13705
13713
13721
13729
13737
13745
13753
13761
13769
13777
13785
13793
13801
13809
13817
13825
13833
13841
13849
13857
13865
13873
13881
13889
13897
13905
13913
13921
13929
13937
13945
13953
13961
13969
13977
13985
13993
14001
14009
14017
14025
14033
14041
14049
14057
14065
14073
14081
14089
14097
14105
1411

23713
23721
23729
23737
23745
23753
23761
23769
23777
23785
23793
23801
23809
23817
23825
23833
23841
23849
23857
23865
23873
23881
23889
23897
23905
23913
23921
23929
23937
23945
23953
23961
23969
23977
23985
23993
24001
24009
24017
24025
24033
24041
24049
24057
24065
24073
24081
24089
24097
24105
24113
24121
24129
24137
24145
24153
24161
24169
24177
24185
24193
24201
24209
24217
24225
24233
24241
24249
24257
24265
24273
24281
24289
24297
24305
24313
24321
24329
24337
24345
24353
24361
24369
24377
24385
24393
24401
24409
24417
24425
24433
24441
24449
24457
24465
24473
24481
24489
24497
24505
24513
24521
24529
24537
24545
24553
24561
24569
24577
24585
24593
24601
24609
24617
24625
24633
24641
24649
24657
24665
24673
24681
24689
24697
24705
24713
24721
24729
24737
24745
24753
24761
24769
24777
24785
24793
24801
24809
24817
24825
24833
24841
24849
24857
24865
24873
24881
24889
24897
24905
24913
24921
24929
24937
24945
24953
24961
24969
24977
24985
24993
25001
25009
25017
25025
25033
2504

34641
34649
34657
34665
34673
34681
34689
34697
34705
34713
34721
34729
34737
34745
34753
34761
34769
34777
34785
34793
34801
34809
34817
34825
34833
34841
34849
34857
34865
34873
34881
34889
34897
34905
34913
34921
34929
34937
34945
34953
34961
34969
34977
34985
34993
35001
35009
35017
35025
35033
35041
35049
35057
35065
35073
35081
35089
35097
35105
35113
35121
35129
35137
35145
35153
35161
35169
35177
35185
35193
35201
35209
35217
35225
35233
35241
35249
35257
35265
35273
35281
35289
35297
35305
35313
35321
35329
35337
35345
35353
35361
35369
35377
35385
35393
35401
35409
35417
35425
35433
35441
35449
35457
35465
35473
35481
35489
35497
35505
35513
35521
35529
35537
35545
35553
35561
35569
35577
35585
35593
35601
35609
35617
35625
35633
35641
35649
35657
35665
35673
35681
35689
35697
35705
35713
35721
35729
35737
35745
35753
35761
35769
35777
35785
35793
35801
35809
35817
35825
35833
35841
35849
35857
35865
35873
35881
35889
35897
35905
35913
35921
35929
35937
35945
35953
35961
3596

In [107]:
df

Name
0                       10th Street Peated Single Malt 
1                1770 Glasgow Single Malt  2019 Release
2      1770 Glasgow Single Malt - Peated  Release No. 1
3                 1792 Full Proof  Single Barrel Select
4     A Distillery in Orkney 2011 MMcK  Càrn Mòr - S...
...                                                 ...
5386                       Yoichi 2019  Limited Edition
5387                 Zippin Blended Malt Scotch Whisky 
5388                              Ærø Whisky Royal Oak 
5389                            Ærø Whisky Single Cask 
5390                                 Ærø Whisky Ærø Eg 

[5391 rows x 1 columns]

In [109]:
df['Stated Age'] = stated_age

In [112]:
df['Strength'] = strength

In [113]:
df.head(20)

Name Stated Age     Strength
0                     10th Street Peated Single Malt         NaN  46.0 % Vol.
1              1770 Glasgow Single Malt  2019 Release        NaN  46.0 % Vol.
2    1770 Glasgow Single Malt - Peated  Release No. 1        NaN  46.0 % Vol.
3               1792 Full Proof  Single Barrel Select        NaN  62.5 % Vol.
4   A Distillery in Orkney 2011 MMcK  Càrn Mòr - S...        NaN  54.8 % Vol.
5   A Dream of Scotland 16-year-old BW  Happy Hall...         16  56.5 % Vol.
6            A Dream of Scotland 2002 BW  Autumn Lady         17  50.2 % Vol.
7          A Dream of Scotland 2006 BW  Unknown Islay         12  56.8 % Vol.
8          A Dream of Scotland 2006 BW  Unknown Islay         13  57.3 % Vol.
9           A Dream of Scotland 2011 BW  The Evil One         07  56.3 % Vol.
10  A Dream of Scotland 2012 BW  Unknown North Isl...         07  58.9 % Vol.
11  A Dream of Scotland Islay Cask Strength BW  Ba...        NaN  55.7 % Vol.
12  A Dream of Scotland Islay Cask Strength BW  Ba...        NaN  56.4 % Vol.
13  A Dream of Scotland Islay Cask Strength BW  Ba...        NaN  56.8 % Vol.
14      A Dream of Scotland The Old Lady of Islay BW          10  48.2 % Vol.
15          A Speyside Malt 2001 CA  In The Courtyard         17  56.4 % Vol.
16     Aberfeldy 15-year-old  Exceptional Cask Series         15  43.0 % Vol.
17             Aberfeldy 15-year-old  Limited Edition         15  43.0 % Vol.
18  Aberfeldy 1995 GM  Connoisseurs Choice - Cask ...         24  53.3 % Vol.
19               Aberfeldy 1996 CA  Warehouse Tasting         22  52.0 % Vol.

In [114]:
size = []

for i in range(2, 100, 8):
    s = soup.find_all('td', {'class': 'data text-right'})[i].text
    if s == '':
        size.append('NaN')
    else:
        size.append(s)
    print(i)

2
10
18
26
34
42
50
58
66
74
82
90
98
